# Проект: классификация

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from  sklearn.ensemble import IsolationForest
import plotly.express as px
import warnings
warnings.filterwarnings('ignore')
from sklearn.preprocessing  import LabelEncoder
from sklearn import linear_model 
from sklearn import tree 
from sklearn import ensemble 
from sklearn import metrics 
from sklearn import preprocessing 
from sklearn.model_selection import train_test_split 
from sklearn.feature_selection import SelectKBest, f_classif

## Часть 1. Знакомство с данными, обработка пропусков и выбросов

###  1

In [3]:
df = pd.read_csv('bank_fin.csv', sep = ';')

In [4]:
df.head()

age         job  marital  education default       balance housing loan  \
0   59      admin.  married  secondary      no   2 343,00 $      yes   no   
1   56      admin.  married  secondary      no      45,00 $       no   no   
2   41  technician  married  secondary      no   1 270,00 $      yes   no   
3   55    services  married  secondary      no   2 476,00 $      yes   no   
4   54      admin.  married   tertiary      no     184,00 $       no   no   

   contact  day month  duration  campaign  pdays  previous poutcome deposit  
0  unknown    5   may      1042         1     -1         0  unknown     yes  
1  unknown    5   may      1467         1     -1         0  unknown     yes  
2  unknown    5   may      1389         1     -1         0  unknown     yes  
3  unknown    5   may       579         1     -1         0  unknown     yes  
4  unknown    5   may       673         2     -1         0  unknown     yes

Данные о клиентах банка:

+ age (возраст);

+ job (сфера занятости);

+ marital (семейное положение);

+ education (уровень образования);

+ default (имеется ли просроченный кредит);

+ housing (имеется ли кредит на жильё);

+ loan (имеется ли кредит на личные нужды);

+ balance (баланс).

Данные, связанные с последним контактом в контексте текущей маркетинговой кампании:

+ contact (тип контакта с клиентом);

+ month (месяц, в котором был последний контакт);

+ day (день, в который был последний контакт);

+ duration (продолжительность контакта в секундах).

Прочие признаки:

+ campaign (количество контактов с этим клиентом в течение текущей кампании);

+ pdays (количество пропущенных дней с момента последней маркетинговой кампании до контакта в текущей кампании);

+ previous (количество контактов до текущей кампании)

+ poutcome (результат прошлой маркетинговой кампании).

Целевая переменная deposit

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11162 entries, 0 to 11161
Data columns (total 17 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   age        11162 non-null  int64 
 1   job        11162 non-null  object
 2   marital    11162 non-null  object
 3   education  11162 non-null  object
 4   default    11162 non-null  object
 5   balance    11137 non-null  object
 6   housing    11162 non-null  object
 7   loan       11162 non-null  object
 8   contact    11162 non-null  object
 9   day        11162 non-null  int64 
 10  month      11162 non-null  object
 11  duration   11162 non-null  int64 
 12  campaign   11162 non-null  int64 
 13  pdays      11162 non-null  int64 
 14  previous   11162 non-null  int64 
 15  poutcome   11162 non-null  object
 16  deposit    11162 non-null  object
dtypes: int64(6), object(11)
memory usage: 1.4+ MB


Поиск пропущённых значений

In [6]:

df.isna().sum()

age           0
job           0
marital       0
education     0
default       0
balance      25
housing       0
loan          0
contact       0
day           0
month         0
duration      0
campaign      0
pdays         0
previous      0
poutcome      0
deposit       0
dtype: int64

###  2

В признаке job и education есть пропущенные значения, которые закодированы словом unknown

In [7]:
df['job'].unique()

array(['admin.', 'technician', 'services', 'management', 'retired',
       'blue-collar', 'unemployed', 'entrepreneur', 'housemaid',
       'unknown', 'self-employed', 'student'], dtype=object)

In [8]:
df['education'].unique()

array(['secondary', 'tertiary', 'primary', 'unknown'], dtype=object)

###  3

In [9]:
df['balance']

0         2 343,00 $ 
1            45,00 $ 
2         1 270,00 $ 
3         2 476,00 $ 
4           184,00 $ 
             ...     
11157         1,00 $ 
11158       733,00 $ 
11159        29,00 $ 
11160           0  $ 
11161           0  $ 
Name: balance, Length: 11162, dtype: object

In [10]:
def convert_balance(value):
    if isinstance(value, float):  # Если уже float, оставляем как есть
        return value
    if isinstance(value, str):    # Если строка, обрабатываем
        value = value.strip().replace('$', '').replace(',', '.').replace(' ', '')
        return float(value)

df['balance'] = df['balance'].apply(convert_balance)

Преобразование в тип float значений столбца balance

###  4

In [11]:
df['balance'] = df['balance'].fillna(df['balance'].median())

Заполнение пропусков медиальным значением

###  5

Замена пропусков модальным значением.

In [12]:

df["job"] = df["job"].apply(lambda x: x.replace('unknown', df["job"].mode()[0]))
df["education"] = df["education"].apply(lambda x: x.replace('unknown', df["education"].mode()[0]))


In [13]:
# Находим самую популярную работу и уровень образования
most_popular_job = df['job'].mode()[0]
most_popular_education = df['education'].mode()[0]

# Фильтруем данные
filtered_df = df[(df['job'] == most_popular_job) & (df['education'] == most_popular_education)]

# Рассчитываем средний баланс
average_balance = filtered_df['balance'].mean()

print(f"Самая популярная работа: {most_popular_job}")
print(f"Самый популярный уровень образования: {most_popular_education}")
print(f"Средний баланс для отфильтрованных данных: {average_balance}")

Самая популярная работа: management
Самый популярный уровень образования: secondary
Средний баланс для отфильтрованных данных: 1598.8829787234042


###  6

Поиск выбросов в balance

In [14]:
# Рассчет IQR и границ
Q1, Q3 = df['balance'].quantile([0.25, 0.75])  # Вычисление Q1 и Q3
IQR = Q3 - Q1

lower_bound = round(Q1 - 1.5 * IQR)  # Нижняя граница
upper_bound = round(Q3 + 1.5 * IQR)  # Верхняя граница

print(f"Нижняя граница: {lower_bound}")
print(f"Верхняя граница: {upper_bound}")

Нижняя граница: -2241
Верхняя граница: 4063


In [15]:
df = df[(df['balance'] >= lower_bound) & (df['balance'] <= upper_bound)]
df.shape

(10105, 17)

## Часть 2:  Разведывательный анализ

###  1

Посмотрим, сколько клиентов открыли депозит

In [16]:
deposit_counts = df['deposit'].value_counts()

fig_deposit = px.pie(
    names= deposit_counts.index,
    values= deposit_counts.values,
    title="Распределение депозитов",
    labels={'label': 'Открытие депозита'}
)
    

fig_deposit.show()

### 2

In [17]:
df

age          job  marital  education default  balance housing loan  \
0       59       admin.  married  secondary      no   2343.0     yes   no   
1       56       admin.  married  secondary      no     45.0      no   no   
2       41   technician  married  secondary      no   1270.0     yes   no   
3       55     services  married  secondary      no   2476.0     yes   no   
4       54       admin.  married   tertiary      no    184.0      no   no   
...    ...          ...      ...        ...     ...      ...     ...  ...   
11157   33  blue-collar   single    primary      no      1.0     yes   no   
11158   39     services  married  secondary      no    733.0      no   no   
11159   32   technician   single  secondary      no     29.0      no   no   
11160   43   technician  married  secondary      no      0.0      no  yes   
11161   34   technician  married  secondary      no      0.0      no   no   

        contact  day month  duration  campaign  pdays  previous poutcome  \
0       unknown    5   may      1042         1     -1         0  unknown   
1       unknown    5   may      1467         1     -1         0  unknown   
2       unknown    5   may      1389         1     -1         0  unknown   
3       unknown    5   may       579         1     -1         0  unknown   
4       unknown    5   may       673         2     -1         0  unknown   
...         ...  ...   ...       ...       ...    ...       ...      ...   
11157  cellular   20   apr       257         1     -1         0  unknown   
11158   unknown   16   jun        83         4     -1         0  unknown   
11159  cellular   19   aug       156         2     -1         0  unknown   
11160  cellular    8   may         9         2    172         5  failure   
11161  cellular    9   jul       628         1     -1         0  unknown   

      deposit  
0         yes  
1         yes  
2         yes  
3         yes  
4         yes  
...       ...  
11157      no  
11158      no  
11159      no  
11160      no  
11161      no  

[10105 rows x 17 columns]

Количесвенные переменнные:
+ age
+ balance
+ day (день, в который был последний контакт);
+ campaign (количество контактов с этим клиентом в течение текущей кампании)
+ duration (продолжительность контакта в секундах)
+ pdays (количество пропущенных дней с момента последней маркетинговой кампании до контакта в текущей кампании)
+ previous (количество контактов до текущей кампании)


In [18]:


# Гистограммы для количественных переменных
for column in ['age', 'balance', 'day', 'campaign', 'duration', 'pdays', 'previous']:
    fig = px.histogram(df, x=column, title=f"Распределение {column}", marginal="box")
    fig.update_layout(xaxis_title=column, yaxis_title="Кол-во")
    fig.show()



In [19]:
# Гистограммы для каждой переменной с разбивкой по депозиту
for column in ['age', 'balance', 'day', 'campaign', 'duration', 'pdays', 'previous']:
    fig = px.histogram(df, x=column, color='deposit',
                       title=f"Распределение {column} в зависимости от депозита",
                       labels={'deposit': 'Депозит'})
    fig.update_layout(xaxis_title=column, yaxis_title="Частота")
    fig.show()

Графики  дают представление о распределении и выбросах для количественных переменных:

Возраст (age):

Распределение симметричное с небольшим количеством выбросов в области возрастов выше 70 лет.
Клиенты с возрастом от 30 до 40 лет, чаще берут депозит.

День (day):

Распределение равномерное, без значительных выбросов.

Количество контактов (campaign):

Большинство клиентов имеют 1–3 контакта, но есть явные выбросы выше 10.

Продолжительность контакта (duration):

Значения выше 1000 секунд (примерно 17 минут) могут считаться выбросами.

pdays и previous:

Большинство значений равно -1 или 0 соответственно, что говорит о редком участии клиентов в предыдущих кампаниях. Выбросы наблюдаются для значений выше 200 (pdays) и 10 (previous).

Основная часть клиентов находится в возрасте от 32 до 50 лет (по квартилям). Значения выше 70 могут быть выбросами (в зависимости от бизнес-логики).

### 3

In [20]:
# Извлечение категориальных переменных
categorical_columns = ['job', 'marital', 'education', 'default', 'housing', 'loan', 'contact', 'month', 'poutcome', 'deposit']

# Рассмотрим описательные статистики для категориальных переменных
categorical_stats = df[categorical_columns].describe(include='all')
print(categorical_stats)


               job  marital  education default housing   loan   contact  \
count        10105    10105      10105   10105   10105  10105     10105   
unique          11        3          3       2       2      2         3   
top     management  married  secondary      no      no     no  cellular   
freq          2315     5715       5517    9939    5243   8712      7283   

        month poutcome deposit  
count   10105    10105   10105  
unique     12        4       2  
top       may  unknown      no  
freq     2617     7570    5424  


In [21]:

# Распределение категориальных переменных
for column in categorical_columns[:-1]:  # Исключаем 'deposit' для отдельного анализа
    value_counts = df[column].value_counts().reset_index()
    value_counts.columns = [column, 'count']  # Переименовываем колонки для корректного отображения
    fig = px.bar(value_counts, x=column, y='count',
                 title=f"Распределение {column}", labels={column: column, 'count': 'Частота'})
    fig.update_layout(xaxis_title=column, yaxis_title="Частота")
    fig.show()


In [22]:
# Визуализация категориальных переменных в зависимости от депозита
for column in categorical_columns[:-1]:  # Исключаем 'deposit' для отдельного анализа
    fig = px.histogram(df, x=column, color='deposit', barmode='group',
                       title=f"{column} в зависимости от депозита", labels={'deposit': 'Депозит'})
    fig.update_layout(xaxis_title=column, yaxis_title="Частота")
    fig.show()

На основе предоставленных графиков из скриншотов можно сделать следующие выводы:

 1. Сферы занятости (job)
   - Наиболее распространённые профессии среди клиентов: management, blue-collar и technician.
   - Клиенты из сфер management, technician, и retired чаще открывают депозиты (больше синих столбцов).
   - В то же время клиенты из категорий blue-collar и services реже открывают депозиты (преобладание красных столбцов).

 2. Семейное положение (marital)
   - Наиболее распространённая категория: married (женатые/замужние).
   - Незамужние/неженатые (single) более склонны к открытию депозитов, чем женатые клиенты, несмотря на меньшее общее количество.

 3. Образование (education)
   - Большинство клиентов имеют secondary образование.
   - Клиенты с tertiary (высшим) образованием чаще открывают депозиты по сравнению с остальными группами.

 4. Кредит по умолчанию (default)
   - Большинство клиентов не имеют кредитных обязательств по умолчанию (no).
   - Клиенты с кредитными обязательствами (yes) крайне редко открывают депозиты.

 5. Ипотека (housing)
   - Значительная часть клиентов имеет ипотеку (yes), но те, у кого нет ипотеки, чаще открывают депозиты.

 6. Потребительский кредит (loan)
   - Большинство клиентов не имеют потребительских кредитов (no).
   - Клиенты без потребительских кредитов чаще открывают депозиты.

 7. Тип контакта (contact)
   - Основной способ связи — cellular (мобильный телефон).
   - Клиенты, с которыми связываются через мобильный телефон, чаще открывают депозиты.

 8. Месяц проведения кампании (month)
   - Кампании чаще всего проводились в мае (may).
   - Самые успешные месяцы для открытия депозитов: nov (ноябрь) и aug (август).

 9. Результат предыдущей кампании (poutcome)
   - Для большинства клиентов результат предыдущей кампании неизвестен (unknown).
   - Если результат предыдущей кампании был success (успешным), вероятность открытия депозита значительно выше.

 Итоговые выводы:
- Клиенты с высоким уровнем образования (tertiary), без кредитов (loan, default) и без ипотеки (housing) имеют больше шансов открыть депозит.
- Использование мобильной связи (cellular) более эффективно для привлечения клиентов.
- Месяц проведения кампании влияет на успех — наиболее продуктивные месяцы для депозитов: nov и aug.

Если нужны дополнительные интерпретации или расчёты, напишите!

### 4

In [23]:
# Группировка по результату предыдущей кампании (poutcome) и текущему результату (deposit)
comparison = df.groupby(['poutcome', 'deposit']).size().unstack(fill_value=0)

# Вычисляем разницу между успехами и неудачами для каждого статуса предыдущей кампании
comparison['success_vs_failure'] = comparison['yes'] - comparison['no']

# Сброс индекса для работы с визуализацией
comparison = comparison.reset_index()

# Визуализация успехов и неудач текущей кампании в зависимости от предыдущей
fig = px.bar(
    comparison.melt(id_vars='poutcome', value_vars=['yes', 'no'], var_name='Current Campaign Result', value_name='Count'),
    x='poutcome', y='Count', color='Current Campaign Result',
    title="Результаты текущей кампании в зависимости от результата предыдущей",
    barmode='group',
    labels={'poutcome': 'Результат предыдущей кампании', 'Count': 'Частота'}
)
fig.show()

# Визуализация разницы между успехами и неудачами
fig = px.bar(
    comparison, x='poutcome', y='success_vs_failure',
    title="Разница между успехами и неудачами текущей кампании",
    labels={'poutcome': 'Результат предыдущей кампании', 'success_vs_failure': 'Разница успехов и неудач'},
    color='success_vs_failure', color_continuous_scale='Bluered'
)
fig.show()

### 5

In [24]:
# Группировка данных по месяцам и результатам текущей кампании
monthly_results = df.groupby(['month', 'deposit']).size().unstack(fill_value=0).reset_index()



# Визуализация распределения успехов и неудач по месяцам
fig = px.bar(
    monthly_results.melt(id_vars='month', value_vars=['yes', 'no'], var_name='Campaign Result', value_name='Count'),
    x='month', y='Count', color='Campaign Result',
    title="Результаты маркетинговых кампаний по месяцам",
    barmode='group',
    labels={'month': 'Месяц', 'Count': 'Частота', 'Campaign Result': 'Результат'}
)
fig.update_layout(xaxis={'categoryorder': 'array', 'categoryarray': ['jan', 'feb', 'mar', 'apr', 'may', 'jun', 'jul', 'aug', 'sep', 'oct', 'nov', 'dec']})
fig.show()




Можем увидеть, что в мае одновременно самый большой процент неудач при взаимодействии в текущей маркетинговой кампании

### 6

In [25]:
# Создание новой переменной для возрастных категорий
df['age_group'] = pd.cut(
    df['age'],
    bins=[0, 30, 40, 50, 60, float('inf')],
    labels=['<30', '30-40', '40-50', '50-60', '60+']
)

# Группировка по возрастным категориям и результатам депозита
age_group_results = df.groupby(['age_group', 'deposit']).size().unstack(fill_value=0).reset_index()

# Визуализация распределения депозитов по возрастным группам
fig = px.bar(
    age_group_results.melt(id_vars='age_group', value_vars=['yes', 'no'], var_name='Deposit Result', value_name='Count'),
    x='age_group', y='Count', color='Deposit Result',
    title="Распределение депозитов по возрастным группам",
    barmode='group',
    labels={'age_group': 'Возрастная группа', 'Count': 'Частота', 'Deposit Result': 'Результат'}
)
fig.show()

###  7

In [26]:
# Функция для построения визуализаций
def visualize_deposit_by_category(column, title):
    category_results = df.groupby([column, 'deposit']).size().unstack(fill_value=0).reset_index()
    fig = px.bar(
        category_results.melt(id_vars=column, value_vars=['yes', 'no'], var_name='Deposit Result', value_name='Count'),
        x=column, y='Count', color='Deposit Result',
        title=title,
        barmode='group',
        labels={column: column.capitalize(), 'Count': 'Количество', 'Deposit Result': 'Результат'}
    )
    fig.show()

# Семейное положение
visualize_deposit_by_category('marital', "Распределение депозитов по семейному положению")

# Уровень образования
visualize_deposit_by_category('education', "Распределение депозитов по уровню образования")

# Сфера занятости
visualize_deposit_by_category('job', "Распределение депозитов по сфере занятости")

###  8

Посмотрим на пересечение категорий

In [27]:



# Создание сводных таблиц
pivot_yes = df[df['deposit'] == 'yes'].pivot_table(index='marital', columns='education', aggfunc='size', fill_value=0)
pivot_no = df[df['deposit'] == 'no'].pivot_table(index='marital', columns='education', aggfunc='size', fill_value=0)



# Тепловая карта для тех, кто открыл депозит
fig_yes = px.imshow(
    pivot_yes.values,
    labels=dict(x="Уровень образования", y="Семейное положение", color="Количество"),
    x=pivot_yes.columns,
    y=pivot_yes.index,
    title="Тепловая карта для клиентов, открывших депозит"
)
fig_yes.update_layout(coloraxis_colorbar=dict(title="Количество"))
fig_yes.show()

# Тепловая карта для тех, кто не открыл депозит
fig_no = px.imshow(
    pivot_no.values,
    labels=dict(x="Уровень образования", y="Семейное положение", color="Количество"),
    x=pivot_no.columns,
    y=pivot_no.index,
    title="Тепловая карта для клиентов, не открывших депозит"
)
fig_no.update_layout(coloraxis_colorbar=dict(title="Количество"))
fig_no.show()


Можем увидеть, что самое мночисленное пересечение категорий это : married и secondary

## Часть 3: преобразование данных

###  1

In [28]:
# преобразуйте уровни образования
le = LabelEncoder()
df['education'] = le.fit_transform(df['education'])

In [29]:
df['age_group'] = le.fit_transform(df['age_group'])

### 2

In [30]:
df['default'] = df['default'].map({'yes': 1, 'no': 0})
df['housing'] = df['housing'].map({'yes': 1, 'no': 0})
df['loan'] = df['loan'].map({'yes': 1, 'no': 0})
df['deposit'] = df['deposit'].map({'yes': 1, 'no': 0})


In [31]:
df

age          job  marital  education  default  balance  housing  loan  \
0       59       admin.  married          1        0   2343.0        1     0   
1       56       admin.  married          1        0     45.0        0     0   
2       41   technician  married          1        0   1270.0        1     0   
3       55     services  married          1        0   2476.0        1     0   
4       54       admin.  married          2        0    184.0        0     0   
...    ...          ...      ...        ...      ...      ...      ...   ...   
11157   33  blue-collar   single          0        0      1.0        1     0   
11158   39     services  married          1        0    733.0        0     0   
11159   32   technician   single          1        0     29.0        0     0   
11160   43   technician  married          1        0      0.0        0     1   
11161   34   technician  married          1        0      0.0        0     0   

        contact  day month  duration  campaign  pdays  previous poutcome  \
0       unknown    5   may      1042         1     -1         0  unknown   
1       unknown    5   may      1467         1     -1         0  unknown   
2       unknown    5   may      1389         1     -1         0  unknown   
3       unknown    5   may       579         1     -1         0  unknown   
4       unknown    5   may       673         2     -1         0  unknown   
...         ...  ...   ...       ...       ...    ...       ...      ...   
11157  cellular   20   apr       257         1     -1         0  unknown   
11158   unknown   16   jun        83         4     -1         0  unknown   
11159  cellular   19   aug       156         2     -1         0  unknown   
11160  cellular    8   may         9         2    172         5  failure   
11161  cellular    9   jul       628         1     -1         0  unknown   

       deposit  age_group  
0            1          2  
1            1          2  
2            1          1  
3            1          2  
4            1          2  
...        ...        ...  
11157        0          0  
11158        0          0  
11159        0          0  
11160        0          1  
11161        0          0  

[10105 rows x 18 columns]

Преобразовал в бинарные переменные

###  3


In [32]:

df = pd.get_dummies(df, columns=['job', 'marital', 'contact', 'month', 'poutcome'], dtype='int')

Создадим дамми-переменные

### 4


In [33]:
fig_cor = px.imshow(
    df.corr(),
    labels=dict(x="Признак", y="Признак", color="Коэффициент корреляции"),
    
)
    
fig_cor.show()

In [34]:
fig_cor_ranking = px.bar(
    df.corr()['deposit'].sort_values(ascending=False),
    labels=dict(x="Признак", y="Коэффициент корреляции"),
)
fig_cor_ranking.show()

Построил матрицу корреляций и столбчатую диаграмму, можем увидеть, что мультиколлинеарность отсутсвует.

### 5

In [35]:
df

age  education  default  balance  housing  loan  day  duration  \
0       59          1        0   2343.0        1     0    5      1042   
1       56          1        0     45.0        0     0    5      1467   
2       41          1        0   1270.0        1     0    5      1389   
3       55          1        0   2476.0        1     0    5       579   
4       54          2        0    184.0        0     0    5       673   
...    ...        ...      ...      ...      ...   ...  ...       ...   
11157   33          0        0      1.0        1     0   20       257   
11158   39          1        0    733.0        0     0   16        83   
11159   32          1        0     29.0        0     0   19       156   
11160   43          1        0      0.0        0     1    8         9   
11161   34          1        0      0.0        0     0    9       628   

       campaign  pdays  ...  month_jun  month_mar  month_may  month_nov  \
0             1     -1  ...          0          0          1          0   
1             1     -1  ...          0          0          1          0   
2             1     -1  ...          0          0          1          0   
3             1     -1  ...          0          0          1          0   
4             2     -1  ...          0          0          1          0   
...         ...    ...  ...        ...        ...        ...        ...   
11157         1     -1  ...          0          0          0          0   
11158         4     -1  ...          1          0          0          0   
11159         2     -1  ...          0          0          0          0   
11160         2    172  ...          0          0          1          0   
11161         1     -1  ...          0          0          0          0   

       month_oct  month_sep  poutcome_failure  poutcome_other  \
0              0          0                 0               0   
1              0          0                 0               0   
2              0          0                 0               0   
3              0          0                 0               0   
4              0          0                 0               0   
...          ...        ...               ...             ...   
11157          0          0                 0               0   
11158          0          0                 0               0   
11159          0          0                 0               0   
11160          0          0                 1               0   
11161          0          0                 0               0   

       poutcome_success  poutcome_unknown  
0                     0                 1  
1                     0                 1  
2                     0                 1  
3                     0                 1  
4                     0                 1  
...                 ...               ...  
11157                 0                 1  
11158                 0                 1  
11159                 0                 1  
11160                 0                 0  
11161                 0                 1  

[10105 rows x 46 columns]

In [36]:
X = df.drop(['deposit'], axis=1)
y = df['deposit']
 
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state = 42, test_size = 0.33)

Разделил выборку на обучающую и тестовую

### 6

In [37]:
selector = SelectKBest(score_func=f_classif, k=15)
selector.fit(X_train, y_train)
X_train = selector.transform(X_train)
X_test = selector.transform(X_test)
columns = selector.get_feature_names_out()
columns



array(['balance', 'housing', 'duration', 'campaign', 'pdays', 'previous',
       'age_group', 'contact_cellular', 'contact_unknown', 'month_mar',
       'month_may', 'month_oct', 'month_sep', 'poutcome_success',
       'poutcome_unknown'], dtype=object)

Отбор 15-ти признаков с помощью SelectorKBest

### 7

In [38]:
scaler = preprocessing.MinMaxScaler()
scaler.fit(X_train)
X_train_scaled = scaler.transform(X_train)
X_test_scaled = scaler.transform(X_test)
# возвращаем имена столбцов
X_train_scaled = pd.DataFrame(X_train_scaled, columns=columns)
X_test_scaled = pd.DataFrame(X_test_scaled, columns=columns)

Нормализация данных

# Часть 4: Решение задачи классификации: логистическая регрессия и решающие деревья

###  1

Обучим алгоритм логистической регрессии

In [39]:
log_reg = linear_model.LogisticRegression(solver="sag", random_state=42)
log_reg.fit(X_train_scaled, y_train)
y_test_pred = log_reg.predict(X_test_scaled)
print("accuracy на тестовом наборе: {:.2f}".format(log_reg.score(X_test_scaled, y_test)))

accuracy на тестовом наборе: 0.81


### 2

Обучим алгоритм решающих деревьев

In [40]:
dt_clf = tree.DecisionTreeClassifier(criterion='entropy', random_state=42)
dt_clf.fit(X_train_scaled, y_train)
y_test_pred = dt_clf.predict(X_test_scaled)
y_train_pred = dt_clf.predict(X_train_scaled)
print(metrics.classification_report(y_test, y_test_pred))
print(metrics.classification_report(y_train, y_train_pred))

              precision    recall  f1-score   support

           0       0.76      0.77      0.77      1790
           1       0.73      0.72      0.73      1545

    accuracy                           0.75      3335
   macro avg       0.75      0.75      0.75      3335
weighted avg       0.75      0.75      0.75      3335

              precision    recall  f1-score   support

           0       1.00      1.00      1.00      3634
           1       1.00      1.00      1.00      3136

    accuracy                           1.00      6770
   macro avg       1.00      1.00      1.00      6770
weighted avg       1.00      1.00      1.00      6770



Можем наблюдать переобучение

### 3

Подберём оптимальные параметры с помощью gridsearch

In [41]:

from sklearn.model_selection import GridSearchCV

param_grid = {
    'min_samples_split': [2, 5, 7, 10],
    'max_depth':[3,5,7]
}

grid_search = GridSearchCV(
    estimator=tree.DecisionTreeClassifier(
        criterion='entropy', 
        random_state=42
        ),
    param_grid=param_grid 
)
grid_search.fit(X_train_scaled, y_train)
print("Наилучшие значения параметров: {}".format(grid_search.best_params_))
y_test_pred = grid_search.predict(X_test_scaled)
print('f1_score на тестовом наборе: {:.2f}'.format(metrics.f1_score(y_test, y_test_pred)))

Наилучшие значения параметров: {'max_depth': 7, 'min_samples_split': 10}
f1_score на тестовом наборе: 0.80


# Часть 5: Решение задачи классификации: ансамбли моделей и построение прогноза

###  1

Обучение случайного леса


In [ ]:
rf_clf = ensemble.RandomForestClassifier(
    n_estimators=100,
    criterion='gini', 
    max_depth=10, 
    min_samples_leaf=5,
    random_state=42 
)

rf_clf.fit(X_train_scaled, y_train)

y_test_pred = rf_clf.predict(X_test_scaled)

print(metrics.classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.85      0.82      0.84      1790
           1       0.80      0.83      0.82      1545

    accuracy                           0.83      3335
   macro avg       0.83      0.83      0.83      3335
weighted avg       0.83      0.83      0.83      3335



### 2

Обучение градиентного бустинга

In [47]:

from sklearn.ensemble import GradientBoostingClassifier

gbc = GradientBoostingClassifier(
    learning_rate=0.05,
    n_estimators=300,
    min_samples_leaf=5,
    max_depth=5,
    random_state=42
)

gbc.fit(X_train_scaled, y_train)

y_test_pred  = gbc.predict(X_test_scaled)

print(metrics.classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.85      0.82      0.84      1790
           1       0.80      0.83      0.82      1545

    accuracy                           0.83      3335
   macro avg       0.83      0.83      0.83      3335
weighted avg       0.83      0.83      0.83      3335



### 3 

Объединим модель с помощью стекинга

In [49]:

from sklearn.ensemble import StackingClassifier
#Создаем список кортежей вида: (наименование модели, модель)
estimators = [
    ('dt_clf',  tree.DecisionTreeClassifier(
        criterion='entropy', 
        max_depth=7, 
        random_state=42)
     ),
    ('logreg', linear_model.LogisticRegression(
        solver='sag', 
        random_state=42, 
        max_iter=1000)
     ),
    ('gbc',  GradientBoostingClassifier(
    learning_rate=0.05,
    n_estimators=300,
    min_samples_leaf=5,
    max_depth=5,
    random_state=42)
     )
]
# Создаем объект класса стекинг
stack_clf = StackingClassifier(
    estimators=estimators, 
    final_estimator=linear_model.LogisticRegression(
        solver='sag', 
        random_state=42, 
        max_iter=1000
    )
)

stack_clf.fit(X_train_scaled, y_train)
y_test_pred  = stack_clf.predict(X_test_scaled)

print(metrics.classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.84      0.84      0.84      1790
           1       0.81      0.81      0.81      1545

    accuracy                           0.82      3335
   macro avg       0.82      0.82      0.82      3335
weighted avg       0.82      0.82      0.82      3335



### 4

Оценим, какие признаки демонстрируют наибольшую важность в модели градиентного бустинга

In [50]:
from sklearn.feature_selection import RFE
estimator = GradientBoostingClassifier()
selector = RFE(estimator, n_features_to_select=3, step=1)
selector.fit(X_train_scaled, y_train)
selector.get_feature_names_out()

array(['duration', 'contact_unknown', 'poutcome_success'], dtype=object)

### 5

Применим фреймворк optuna для оптимизации гиперпараметров

In [52]:
import optuna

# реализуйте оптимизацию гиперпараметров с помощью Optuna
def optuna_rf(trial):
  # задаем пространства поиска гиперпараметров
  n_estimators = trial.suggest_int('n_estimators', 100, 200, 1)
  max_depth = trial.suggest_int('max_depth', 10, 30, 1)
  min_samples_leaf = trial.suggest_int('min_samples_leaf', 2, 10, 1)

  # создаем модель
  model = ensemble.RandomForestClassifier(n_estimators=n_estimators,
                                          max_depth=max_depth,
                                          min_samples_leaf=min_samples_leaf,
                                          random_state=42)
  # обучаем модель
  model.fit(X_train_scaled, y_train)
  score = metrics.f1_score(y_train, model.predict(X_train_scaled))

  return score

# cоздаем объект исследования
# можем напрямую указать, что нам необходимо максимизировать метрику direction="maximize"
study = optuna.create_study(study_name="RandomForestClassifier", direction="maximize")
# ищем лучшую комбинацию гиперпараметров n_trials раз
study.optimize(optuna_rf, n_trials=20)
print("Наилучшие значения гиперпараметров {}".format(study.best_params))

model = ensemble.RandomForestClassifier(**study.best_params, random_state=42)
model.fit(X_train_scaled, y_train)
y_test_pred = model.predict(X_test_scaled)
print(metrics.classification_report(y_test, y_test_pred))

[I 2025-01-10 13:51:12,442] A new study created in memory with name: RandomForestClassifier
[I 2025-01-10 13:51:12,919] Trial 0 finished with value: 0.8466007222483907 and parameters: {'n_estimators': 145, 'max_depth': 19, 'min_samples_leaf': 10}. Best is trial 0 with value: 0.8466007222483907.
[I 2025-01-10 13:51:13,453] Trial 1 finished with value: 0.8460693550917935 and parameters: {'n_estimators': 163, 'max_depth': 27, 'min_samples_leaf': 10}. Best is trial 0 with value: 0.8466007222483907.
[I 2025-01-10 13:51:13,875] Trial 2 finished with value: 0.8512772292744084 and parameters: {'n_estimators': 125, 'max_depth': 11, 'min_samples_leaf': 6}. Best is trial 2 with value: 0.8512772292744084.
[I 2025-01-10 13:51:14,392] Trial 3 finished with value: 0.8768580816773588 and parameters: {'n_estimators': 135, 'max_depth': 18, 'min_samples_leaf': 4}. Best is trial 3 with value: 0.8768580816773588.
[I 2025-01-10 13:51:14,814] Trial 4 finished with value: 0.8492808005003127 and parameters: {'

Наилучшие значения гиперпараметров {'n_estimators': 175, 'max_depth': 26, 'min_samples_leaf': 2}
              precision    recall  f1-score   support

           0       0.85      0.81      0.83      1790
           1       0.80      0.84      0.82      1545

    accuracy                           0.83      3335
   macro avg       0.82      0.83      0.82      3335
weighted avg       0.83      0.83      0.83      3335

